In [ ]:
import pygame
import pygame
import numpy as np

In [ ]:
NAME = "Flock"
DIMENTIONS = (800, 500)#(1100, 800)
WHITE = (255, 255, 255)
GREEN = (34,139,34) #(0, 154, 23)
GREY = (10, 10, 1)
BLACK = (0, 0, 0)

In [ ]:
circle_radius = 30  
circle_color = GREY

In [ ]:
class Sheep:

    def __init__(self):
        self.size = 5
        self.mass = 1
        self.position = np.array([np.random.randint(100, 300), np.random.randint(100, 300)], dtype=float) # np.array([DIMENTIONS[0]//2, DIMENTIONS[1]//2], dtype=float)
        self.velocity = np.array([0, 0], dtype=float)
        self.accel = np.array([0, 0], dtype=float)

        self.maxSpeed = 4

        self.maxForce = 0.7

        self.alert_dist = 100

        self.global_alpha = 0.000001

    def random_unit_vector(self):
        angle = np.random.uniform(0, 2 * np.pi)  # Random angle in radians
        x = np.cos(angle)
        y = np.sin(angle)
        return np.array([x, y])
        
    def dist_to(self, sheep2):
        return np.linalg.norm(self.position - sheep2.position)
    
    def _get_flock_center(self, local_sheep_list):
        if len(local_sheep_list) == 0:
            return self.position
        center = np.sum([sheep.position for sheep in local_sheep_list], axis=0) / len(local_sheep_list)
        return center
    
    def _get_flock_velocity(self, local_sheep_list):
        if len(local_sheep_list) == 0:
            return self.velocity
        avg_velocity = np.sum([sheep.velocity for sheep in local_sheep_list], axis=0) / len(local_sheep_list)
        return avg_velocity
    
    def _limit_steering_force(self, steering_force):
        if np.linalg.norm(steering_force) > self.maxForce:
            return steering_force / np.linalg.norm(steering_force) * self.maxForce
        return steering_force

    def find_local_sheep_list(self, sheep_list, local_r):

        local_sheep_list = []

        for other_sheep in sheep_list:
            
            sheep_dist = self.dist_to(other_sheep)

            if sheep_dist > 0 and sheep_dist < local_r:
                local_sheep_list.append(other_sheep)
        
        return local_sheep_list
    
    def alignment_behavior(self, local_sheep_list):
        local_avg_velocity = self._get_flock_velocity(local_sheep_list)
        desired_dir = local_avg_velocity / (np.linalg.norm(local_avg_velocity) + self.global_alpha)
        desired_vel = desired_dir * self.maxSpeed

        steering_force = (desired_vel - self.velocity) 

        return self._limit_steering_force(steering_force)

    def cohesion_behavior(self, local_sheep_list):
        local_center = self._get_flock_center(local_sheep_list)
        return self.seek_behavior(local_center)
    
    def separation_behavior(self, local_sheep_list):

        separate_force_weighted_sum = np.array([0, 0], dtype=float)

        for other_sheep in local_sheep_list:
            dist_to_other_sheep = self.dist_to(other_sheep)
            # separate_force_weighted_sum inversly proportional to distance, if dist is small, separation force should be large
            separate_force_weighted_sum += (self.position - other_sheep.position) / (dist_to_other_sheep + self.global_alpha) 

        separte_dir = separate_force_weighted_sum / (np.linalg.norm(separate_force_weighted_sum) + self.global_alpha)
        desired_vel = separte_dir * self.maxSpeed

        steering_force = (desired_vel - self.velocity)

        return self._limit_steering_force(steering_force)


    def seek_behavior(self, target):
        
        desired_dir = (target - self.position) / (np.linalg.norm(target - self.position) + self.global_alpha)
        desired_vel = desired_dir * self.maxSpeed

        steering_force = (desired_vel - self.velocity) 

        return self._limit_steering_force(steering_force)
    
    def arrive_behavior(self, target, threshold_r=20):
        dist_to_target = np.linalg.norm(target - self.position)

        desired_dir = (target - self.position) / (np.linalg.norm(target - self.position) + self.global_alpha)
        if dist_to_target < threshold_r:
            desired_vel = desired_dir * self.maxSpeed * (dist_to_target / threshold_r)
        else:
            desired_vel = desired_dir * self.maxSpeed
        
        steering_force = (desired_vel - self.velocity) 

        return self._limit_steering_force(steering_force)
    

    def flee_behavior(self, target):
        dist_to_target = np.linalg.norm(target - self.position)
        if dist_to_target < self.alert_dist:
            return - self.seek_behavior(target)
        return np.array([0, 0], dtype=float)

    
    def apply_force(self, steering_force):
        # # limit maxForce
        # accel_dir = steering_force / (np.linalg.norm(steering_force) + self.global_alpha)
        # self.accel += accel_dir * self.maxForce / self.mass

        self.accel += steering_force / self.mass

    def limit_velocity(self):
        # if np.linalg.norm(self.accel) == 0:
        #     self.velocity = np.array([0, 0], dtype=float) 
        if np.linalg.norm(self.velocity) > self.maxSpeed:
            self.velocity = self.velocity / np.linalg.norm(self.velocity) * self.maxSpeed
    
    def edge(self):
        self.position[0] = self.position[0] % DIMENTIONS[0]
        self.position[1] = self.position[1] % DIMENTIONS[1]
        # self.position[0] = max(1, min(self.position[0], DIMENTIONS[0] - 1))
        # self.position[1] = max(1, min(self.position[1], DIMENTIONS[1] - 1))
        
    def update(self):
        self.velocity += self.accel
        self.limit_velocity()
        self.position += self.velocity
        self.edge()
        self.accel = np.array([0, 0], dtype=float)

    def draw(self, canvas, color=WHITE):
        pygame.draw.circle(canvas, color, self.position, self.size)
    
        

In [ ]:
class Flock:

    alignment_weight = 1
    cohesion_weight = 1
    separation_weight = 1
    flee_weight = 1
    
    def __init__(self, num):
        self.sheep_num = num
        self.sheep_list = [Sheep() for _ in range(num)]         

    def alignment(self, local_r=200):

        alignment_force_list = []

        for i in range(self.sheep_num):

            sheep1 = self.sheep_list[i]
            local_sheep_list = sheep1.find_local_sheep_list(self.sheep_list, local_r)
            alignment_force_list.append(sheep1.alignment_behavior(local_sheep_list))

        return alignment_force_list

    
    def cohesion(self, local_r=200):
        # steering towards average position of local flock-mates, local range defined by local_r

        cohesion_force_list = []

        for i in range(self.sheep_num):

            sheep1 = self.sheep_list[i]
            local_sheep_list = sheep1.find_local_sheep_list(self.sheep_list, local_r)
            cohesion_force_list.append(sheep1.cohesion_behavior(local_sheep_list))
            
        return cohesion_force_list
    
    def separation(self, local_r=30):

        separation_force_list = []

        for i in range(self.sheep_num):

            sheep1 = self.sheep_list[i]
            local_sheep_list = sheep1.find_local_sheep_list(self.sheep_list, local_r)
            separation_force_list.append(sheep1.separation_behavior(local_sheep_list))
            
        return separation_force_list
    
    def calculate_and_apply_force(self, flee_target, local_r=30):
        separation_force_list = []
        cohesion_force_list = []
        alignment_force_list = []
        flee_force_list = []
        
        for i in range(self.sheep_num):
            sheep1 = self.sheep_list[i]
            local_sheep_list = sheep1.find_local_sheep_list(self.sheep_list, local_r)
            separation_force_list.append(sheep1.separation_behavior(local_sheep_list))
            cohesion_force_list.append(sheep1.cohesion_behavior(local_sheep_list))
            alignment_force_list.append(sheep1.alignment_behavior(local_sheep_list))
            flee_force_list.append(sheep1.flee_behavior(flee_target))
        
        alignment_force_list = np.array(alignment_force_list)
        cohesion_force_list = np.array(cohesion_force_list)
        separation_force_list = np.array(separation_force_list)
        flee_force_list = np.array(flee_force_list)
        weighted_force = Flock.alignment_weight * alignment_force_list + Flock.cohesion_weight * cohesion_force_list + Flock.separation_weight * separation_force_list + Flock.flee_weight * flee_force_list
        for i in range(self.sheep_num):
            self.sheep_list[i].apply_force(weighted_force[i])

        
    # def calculate_and_apply_force2(self, flee_target):
    #     alignment_force_list = np.array(self.alignment())
    #     cohesion_force_list = np.array(self.cohesion())
    #     separation_force_list = np.array(self.separation())
    #     weighted_force = 0.5 * alignment_force_list + 0.5 * cohesion_force_list + 1 * separation_force_list
    #     for i in range(self.sheep_num):
    #         self.sheep_list[i].apply_force(weighted_force[i])
    
    def update(self, flee_target):
        self.calculate_and_apply_force(flee_target)
        for sheep in self.sheep_list:
            sheep.update()

    def draw(self, canvas):
        for sheep in self.sheep_list:
            sheep.draw(canvas)

In [ ]:
flock_main = Flock(100)

In [ ]:
alignment_weight_slider = pygame.Rect(DIMENTIONS[0] - 220, DIMENTIONS[1] - 280, 200, 10)
cohesion_weight_slider = pygame.Rect(DIMENTIONS[0] - 220, DIMENTIONS[1] - 200, 200, 10)
separation_weight_slider = pygame.Rect(DIMENTIONS[0] - 220, DIMENTIONS[1] - 120, 200, 10)
# flee_weight_slider = pygame.Rect(DIMENTIONS[0] - 220, DIMENTIONS[1] - 200, 200, 10)
alignment_weight_value = Flock.alignment_weight
cohesion_weight_value = Flock.cohesion_weight
separation_weight_value = Flock.separation_weight
flee_weight_value = Flock.flee_weight

In [ ]:
# Set up the sliders
max_speed_slider = pygame.Rect(DIMENTIONS[0] - 220, DIMENTIONS[1] - 40, 200, 10)
# max_force_slider = pygame.Rect(DIMENTIONS[0] - 220, DIMENTIONS[1] - 40, 200, 10)
max_speed_value = Sheep().maxSpeed
# max_force_value = Sheep().maxForce
slider_dragging = None

In [ ]:
pygame.init()
pygame.display.set_caption(NAME)
canvas = pygame.display.set_mode(DIMENTIONS)

while True:
    for event in pygame.event.get():
        if event.type == pygame.QUIT:
            pygame.quit()
        elif event.type == pygame.MOUSEBUTTONDOWN:
            if max_speed_slider.collidepoint(event.pos):
                slider_dragging = 'max_speed'
            # elif max_force_slider.collidepoint(event.pos):
            #     slider_dragging = 'max_force'
            elif alignment_weight_slider.collidepoint(event.pos):
                slider_dragging = 'alignment_weight'
            elif cohesion_weight_slider.collidepoint(event.pos):
                slider_dragging = 'cohesion_weight'
            elif separation_weight_slider.collidepoint(event.pos):
                slider_dragging = 'separation_weight'
            # elif flee_weight_slider.collidepoint(event.pos):
            #     slider_dragging = 'flee_weight'
        elif event.type == pygame.MOUSEBUTTONUP:
            slider_dragging = None
        elif event.type == pygame.MOUSEMOTION and slider_dragging:
            if slider_dragging == 'max_speed':
                max_speed_value = max(1, min(20, (event.pos[0] - max_speed_slider.left) / max_speed_slider.width * 20))
            # elif slider_dragging == 'max_force':
            #     max_force_value = max(0.1, min(5, (event.pos[0] - max_force_slider.left) / max_force_slider.width * 5))
            elif slider_dragging == 'alignment_weight':
                alignment_weight_value = max(0, min(4, (event.pos[0] - alignment_weight_slider.left) / alignment_weight_slider.width * 4))
            elif slider_dragging == 'cohesion_weight':
                cohesion_weight_value = max(0, min(4, (event.pos[0] - cohesion_weight_slider.left) / cohesion_weight_slider.width * 4))
            elif slider_dragging == 'separation_weight':
                separation_weight_value = max(0, min(4, (event.pos[0] - separation_weight_slider.left) / separation_weight_slider.width * 4))
            # elif slider_dragging == 'flee_weight':
            #     flee_weight_value = max(0, min(4, (event.pos[0] - flee_weight_slider.left) / flee_weight_slider.width * 4))



    for sheep in flock_main.sheep_list:
        sheep.maxSpeed = max_speed_value
        # sheep.maxForce = max_force_value
    
    Flock.alignment_weight = alignment_weight_value
    Flock.cohesion_weight = cohesion_weight_value
    Flock.separation_weight = separation_weight_value
    # Flock.flee_weight = flee_weight_value
        
    canvas.fill(BLACK)

    # Draw the sliders
    pygame.draw.rect(canvas, (192, 192, 192), max_speed_slider)
    # pygame.draw.rect(canvas, (192, 192, 192), max_force_slider)
    pygame.draw.rect(canvas, (192, 192, 192), alignment_weight_slider)
    pygame.draw.rect(canvas, (192, 192, 192), cohesion_weight_slider)
    pygame.draw.rect(canvas, (192, 192, 192), separation_weight_slider)
    # pygame.draw.rect(canvas, (192, 192, 192), flee_weight_slider)

    SLIDER_COLOR = GREEN
    # Draw the slider handles
    pygame.draw.rect(canvas, SLIDER_COLOR, (max_speed_slider.left + int((max_speed_value / 20) * max_speed_slider.width) - 10, max_speed_slider.top, 10, 10))
    # pygame.draw.rect(canvas, SLIDER_COLOR, (max_force_slider.left + int((max_force_value / 5) * max_force_slider.width) - 10, max_force_slider.top, 10, 10))
    pygame.draw.rect(canvas, SLIDER_COLOR, (alignment_weight_slider.left + int((alignment_weight_value / 4) * alignment_weight_slider.width) - 10, alignment_weight_slider.top, 10, 10))
    pygame.draw.rect(canvas, SLIDER_COLOR, (cohesion_weight_slider.left + int((cohesion_weight_value / 4) * cohesion_weight_slider.width) - 10, cohesion_weight_slider.top, 10, 10))
    pygame.draw.rect(canvas, SLIDER_COLOR, (separation_weight_slider.left + int((separation_weight_value / 4) * separation_weight_slider.width) - 10, separation_weight_slider.top, 10, 10))
    # pygame.draw.rect(canvas, SLIDER_COLOR, (flee_weight_slider.left + int((flee_weight_value / 4) * flee_weight_slider.width) - 10, flee_weight_slider.top, 10, 20))

    # Display values and names
    font = pygame.font.Font(None, 24)
    text_speed = font.render(f"Max Speed: {max_speed_value:.2f}", True, WHITE)
    # text_force = font.render(f"Max Force: {max_force_value:.2f}", True, WHITE)
    canvas.blit(text_speed, (max_speed_slider.left, max_speed_slider.top - 30))
    # canvas.blit(text_force, (max_force_slider.left, max_force_slider.top - 30))

    text_alig = font.render(f"Alignment weight: {alignment_weight_value:.2f}", True, WHITE)
    text_cohe = font.render(f"Cohesion weight: {cohesion_weight_value:.2f}", True, WHITE)
    text_sepa = font.render(f"Separation weight: {separation_weight_value:.2f}", True, WHITE)
    # text_flee = font.render(f"Flee weight: {flee_weight_value:.2f}", True, WHITE)
    canvas.blit(text_alig, (alignment_weight_slider.left, alignment_weight_slider.top - 30))
    canvas.blit(text_cohe, (cohesion_weight_slider.left, cohesion_weight_slider.top - 30))
    canvas.blit(text_sepa, (separation_weight_slider.left, separation_weight_slider.top - 30))
    # canvas.blit(text_flee, (flee_weight_slider.left, flee_weight_slider.top - 30))

    
    cursor_position = np.array(pygame.mouse.get_pos())

    flock_main.draw(canvas)
    flock_main.update(flee_target=cursor_position)

    # pygame.draw.circle(canvas, circle_color, cursor_position, circle_radius, 10) 

    pygame.display.update()

    pygame.time.Clock().tick(120)
